In [1]:
# %%
import sys
sys.path.append("..")
import numpy as np
from matplotlib import pyplot as plt
from IPython.display import Audio
import scipy.signal as sg
import librosa
from src.utilities.utils import babble_noise
from mcsm_benchs.Benchmark import Benchmark
from pesq import pesq
from pystoi import stoi
import os
from src.utilities.scale_functions import scale_fun_APF, scale_fun_Fvs, scale_fun_F

# from src.aps_metric.perf_metrics import musical_noise_measure_aps
from src.methods.method_hard_threshold import NewMethod as hard_thresholding
from src.methods.method_garrote_threshold import NewMethod as garrote_thresholding
from src.methods.method_delaunay_triangulation import delaunay_triangulation_denoising 


In [2]:

def dt_method(signal,*args,**kwargs):
    output = delaunay_triangulation_denoising(signal=signal,
                                            mcsim_path='src/utilities/simulations',
                                            *args,**kwargs)
    return output


In [3]:


# Create a dictionary of signals.
signals_dict = {}
N = 1*8192 # A bit more than a second of signal.
for i in range(6,7):
    x,fs = librosa.load('./signals/{}_male.mp3'.format(i), sr=8000)
    x = x[:N]
    signals_dict['{}_male'.format(i)]=x

for i in range(6,7):
    x,fs = librosa.load('./signals/{}_female.mp3'.format(i), sr=8000)
    x = x[:N]
    signals_dict['{}_female'.format(i)]=x

x,fs = librosa.load('./signals/cello.wav', sr=8000)
x = x[500:500+N]
signals_dict['cello']=x

x, fs = librosa.load(librosa.ex('trumpet'), duration=1.5, sr=8000)
x = x[0:N]
signals_dict['trumpet']=x



In [4]:
# Parameters
Nfft = 2*N
thr = np.arange(0.5,5.5,0.5)
lmax = np.arange(1.0,3.25,0.25)
SNRs = [-5, 0, 5, 10, 15, 20]
reps = 50

# %%
dict_methods = {
                'dt': dt_method,
                'ht': hard_thresholding().method,
                # 'st': garrote_thresholding().method,
                }

dict_parameters = {
                    'dt': [{'scale_fun':scale_fun_APF},
                           {'scale_fun':scale_fun_Fvs},
                           {'scale_fun':scale_fun_F},
                           *[{'LB':q} for q in lmax],
                           ],
                    'ht': [{'coeff':q, 'Nfft':2**12} for q in thr],
                    # 'st': [{'coeff':q, 'Nfft':2**12} for q in thr],
                    }

In [5]:
# Once new methods are added, load previous benchmark and add new methods.
new_methods_flag = False
# benchmark = Benchmark.load_benchmark('./results/benchmark_babble')
# benchmark.add_new_method(methods=dict_methods,parameters=dict_parameters)


In [6]:
# Here define performance functions.
# PESQ:
def pesq_metric(x,x_hat,**kwargs):
    # print("It's using pesq!")
    return pesq(fs,x,x_hat,'nb')

# STOI:
def stoi_metric(x,x_hat,**kwargs):
    stoival = stoi(x, x_hat, fs, extended=False)
    return 100/(1+np.exp(-17.4906*stoival+9.6921))

from src.aps_metric.perf_metrics import musical_noise_measure_aps_8
def aps(x,xhat,**kwargs):
    return musical_noise_measure_aps_8(x,xhat,fs=fs,**kwargs)

print(stoi_metric(x,x), pesq_metric(x,x))

perf_funs = {'pesq':pesq_metric,
             'stoi':stoi_metric,
	        #  'aps':aps, # Only compute this at best pesq.
             }

if new_methods_flag:
    benchmark.objectiveFunction = perf_funs
    benchmark.verbosity = 5
    # benchmark.parallel_flag = 2

99.95898182754574 4.548638343811035


In [7]:
# %%
if not new_methods_flag:
    benchmark = Benchmark(task = 'denoising',
                            methods = dict_methods,
                            N = len(x), 
                            SNRin = SNRs, 
                            repetitions = reps,
                            signal_ids= signals_dict,
                            parameters=dict_parameters,
                            verbosity=5, 
                            parallelize=5,
                            obj_fun=perf_funs,
                            complex_noise=babble_noise,                     
                            )
# %%

Number of processors:  12
Parallel pool: 5


In [8]:
benchmark.run() # Run the benchmark

Running benchmark...
- Signal 6_male
-- SNR: -5 dB
--- Parallel loop -- Method: dt(all parameters)
--- Parallel loop -- Method: ht(all parameters)
------ Inner loop. dt: 0
------ Inner loop. dt: 5
------ Inner loop. dt: 10
------ Inner loop. dt: 15
------ Inner loop. dt: 20
------ Inner loop. dt: 16
------ Inner loop. dt: 21
A curve_set(1d) object with 2500 curves observed at 3 argument values
(1 observed, 2499 simulated).
Contains: 
$ r     :  num [1:3] 0.738 0.861 0.984
$ funcs :  num [1:3, 1:2500] 1.37 1.48 1.55 1.39 1.51 ...
 - attr(*, "dimnames")=List of 2
  ..$ : chr [1:3] "7" "8" "9"
  ..$ : chr [1:2500] "obs" "sim1" "sim2" "sim3" ...

Threshold:1.4754638671875
------ Inner loop. dt: 17
------ Inner loop. dt: 22
------ Inner loop. dt: 6
------ Inner loop. dt: 18
A curve_set(1d) object with 2500 curves observed at 3 argument values
(1 observed, 2499 simulated).
Contains: 
$ r     :  num [1:3] 0.738 0.861 0.984
$ funcs :  num [1:3, 1:2500] 0.957 0.993 1 0.969 0.996 ...
 - attr(*, 

{'pesq': {'6_male': {-5: {'dt': {"{'scale_fun': <function scale_fun_APF at 0x761ec6b84b80>}": [1.194094181060791,
      1.1733551025390625,
      1.1968032121658325,
      1.1472601890563965,
      1.1889863014221191,
      1.1859266757965088,
      1.1510636806488037,
      1.1385473012924194,
      1.1513794660568237,
      1.2248916625976562,
      1.114314317703247,
      1.1879478693008423,
      1.1826536655426025,
      1.110945701599121,
      1.1718251705169678,
      1.2030320167541504,
      1.2396414279937744,
      1.2009780406951904,
      1.1692781448364258,
      1.1496411561965942,
      1.1833009719848633,
      1.1742860078811646,
      1.1622825860977173,
      1.1929314136505127,
      1.238116979598999,
      1.2286908626556396,
      1.2136774063110352,
      1.1004743576049805,
      1.2304147481918335,
      1.1977274417877197,
      1.206756353378296,
      1.1376214027404785,
      1.143057107925415,
      1.1602520942687988,
      1.1827702522277832,
      1

In [9]:
benchmark.save_to_file(filename = './results/benchmark_babble')

True

In [10]:
# This formats the results on a DataFrame
results_parameters = benchmark.get_results_as_df()
results_parameters

[      Method                     Parameter Signal_id  Repetition        -5  \
 2500      dt                   {'LB': 1.0}  6_female           0  1.187293   
 2501      dt                   {'LB': 1.0}  6_female           1  1.151145   
 2502      dt                   {'LB': 1.0}  6_female           2  1.215615   
 2503      dt                   {'LB': 1.0}  6_female           3  1.210942   
 2504      dt                   {'LB': 1.0}  6_female           4  1.177212   
 ...      ...                           ...       ...         ...       ...   
 17195     ht  {'coeff': 5.0, 'Nfft': 4096}   trumpet          45  1.117449   
 17196     ht  {'coeff': 5.0, 'Nfft': 4096}   trumpet          46  1.068829   
 17197     ht  {'coeff': 5.0, 'Nfft': 4096}   trumpet          47  1.055722   
 17198     ht  {'coeff': 5.0, 'Nfft': 4096}   trumpet          48  1.062660   
 17199     ht  {'coeff': 5.0, 'Nfft': 4096}   trumpet          49  1.072918   
 
               0         5        10        15    